## Stage 1: Installing dependencies and environment setup


In [5]:
!pip install tensorflow-gpu==2.0.0.alpha0

In [6]:
!pip install pandas-datareader

## Stage 2: Importing project dependencies

In [7]:
import math
import random
import numpy as np
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
import pandas_datareader as data_reader

from tqdm import tqdm_notebook, tqdm
from collections import deque

/home/mohamedalgebali/anaconda3/lib/python3.7/site-packages/pandas_datareader/compat/__init__.py:7: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  from pandas.util.testing import assert_frame_equal


In [8]:
tf.__version__

'2.0.0-alpha0'

## Stage 3: Building the AI Trader network

In [9]:
class AI_Trader():
  
    def __init__(self, state_size, action_space=3, model_name="AITrader"): #Stay, Buy, Sell
    
        self.state_size = state_size
        self.action_space = action_space
        self.memory = deque(maxlen=2000)
        self.inventory = []
        self.model_name = model_name

        self.gamma = 0.95
        self.epsilon = 1.0
        self.epsilon_final = 0.01
        self.epsilon_decay = 0.995

        self.model = self.model_builder()
    
    def model_builder(self):

        model = tf.keras.models.Sequential()

        model.add(tf.keras.layers.Dense(units=32, activation='relu', input_dim=self.state_size))

        model.add(tf.keras.layers.Dense(units=64, activation='relu'))

        model.add(tf.keras.layers.Dense(units=128, activation='relu'))

        model.add(tf.keras.layers.Dense(units=self.action_space, activation='linear'))

        model.compile(loss='mse', optimizer=tf.keras.optimizers.Adam(lr=0.001))

        return model

    def trade(self, state):

        if random.random() <= self.epsilon:
            return random.randrange(self.action_space)

        actions = self.model.predict(state)
        return np.argmax(actions[0])


    def batch_train(self, batch_size):

        batch = []
        for i in range(len(self.memory) - batch_size + 1, len(self.memory)):
            batch.append(self.memory[i])

        for state, action, reward, next_state, done in batch:
            reward = reward
            if not done:
                reward = reward + self.gamma * np.amax(self.model.predict(next_state)[0])

            target = self.model.predict(state)
            target[0][action] = reward

            self.model.fit(state, target, epochs=1, verbose=0)

        if self.epsilon > self.epsilon_final:
            self.epsilon *= self.epsilon_decay

## Stage 4: Dataset preprocessing

### Defining helper functions

#### Sigmoid

In [10]:
def sigmoid(x):
    return 1 / (1 + math.exp(-x))

#### Price format function

In [11]:
def stocks_price_format(n):
    if n < 0:
        return "- $ {0:2f}".format(abs(n))
    else:
        return "$ {0:2f}".format(abs(n))

#### Dataset loader

In [12]:
def dataset_loader(stock_name):
  
  #Complete the dataset loader function
    dataset = data_reader.DataReader(stock_name, data_source="yahoo")
  
    start_date = str(dataset.index[0]).split()[0]
    end_date = str(dataset.index[-1]).split()[0]
  
    close = dataset['Close']

    return close

### State creator

In [13]:
def state_creator(data, timestep, window_size):
  
    starting_id = timestep - window_size + 1
  
    if starting_id >= 0:
        windowed_data = data[starting_id:timestep+1]
    else:
        windowed_data = - starting_id * [data[0]] + list(data[0:timestep+1])
    
    state = []
    for i in range(window_size - 1):
        state.append(sigmoid(windowed_data[i+1] - windowed_data[i]))
    
    return np.array([state])

### Loading a dataset

In [14]:
stock_name = "AAPL"
data = dataset_loader(stock_name)

## Stage 5: Training the AI Trader

### Setting hyper parameters

In [19]:
window_size = 10
episodes = 100

batch_size = 32
data_samples = len(data) - 1

### Defining the Trader model

In [16]:
trader = AI_Trader(window_size)

In [17]:
trader.model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 32)                352       
_________________________________________________________________
dense_1 (Dense)              (None, 64)                2112      
_________________________________________________________________
dense_2 (Dense)              (None, 128)               8320      
_________________________________________________________________
dense_3 (Dense)              (None, 3)                 387       
Total params: 11,171
Trainable params: 11,171
Non-trainable params: 0
_________________________________________________________________


### Training loop

In [20]:
for episode in range(1, episodes + 1):
  
    print("Episode: {}/{}".format(episode, episodes))
  
    state = state_creator(data, 0, window_size + 1)
  
    total_profit = 0
    trader.inventory = []
  
    for t in tqdm(range(data_samples)):
    
        action = trader.trade(state)
    
        next_state = state_creator(data, t+1, window_size + 1)
        reward = 0
    
        if action == 1: #Buying
            trader.inventory.append(data[t])
            print("AI Trader bought: ", stocks_price_format(data[t]))
      
        elif action == 2 and len(trader.inventory) > 0: #Selling
            buy_price = trader.inventory.pop(0)
      
            reward = max(data[t] - buy_price, 0)
            total_profit += data[t] - buy_price
            print("AI Trader sold: ", stocks_price_format(data[t]), " Profit: " + stocks_price_format(data[t] - buy_price) )
      
        if t == data_samples - 1:
            done = True
        else:
            done = False
      
        trader.memory.append((state, action, reward, next_state, done))

        state = next_state
    
        if done:
            print("########################")
            print("TOTAL PROFIT: {}".format(total_profit))
            print("########################")

        if len(trader.memory) > batch_size:
            trader.batch_train(batch_size)

            
trader.model.save("ai_trader.h5")
    


  0%|          | 1/1257 [00:00<02:27,  8.51it/s]

Episode: 1/100
AI Trader bought:  $ 126.000000
AI Trader bought:  $ 125.690002



  0%|          | 3/1257 [00:00<02:18,  9.05it/s]

AI Trader bought:  $ 122.570000
AI Trader bought:  $ 120.070000
AI Trader bought:  $ 123.279999



  1%|          | 7/1257 [00:00<02:07,  9.83it/s]

...

AI Trader bought:  $ 224.369995
AI Trader bought:  $ 246.880005
AI Trader sold:  $ 245.520004  Profit: $ 21.150009



 95%|█████████▍| 1192/1257 [01:49<00:06, 10.61it/s]

AI Trader sold:  $ 258.440002  Profit: $ 11.559998



100%|██████████| 1257/1257 [01:55<00:00, 10.90it/s]

########################
TOTAL PROFIT: 33.12999725341797
########################
